# Installing Z3 and Imports

In [1]:
'''
!pip install z3-solver
!pip install pandas
!pip install numpy
!pip install sklearn
!pip install anchor-exp
'''

'\n!pip install z3-solver\n!pip install pandas\n!pip install numpy\n!pip install sklearn\n!pip install anchor-exp\n'

In [2]:
import pandas as pd
import numpy as np
from sklearn import datasets
from sklearn.model_selection import train_test_split
from sklearn import svm
from sklearn import metrics
from z3 import *

# Training Linear and Polynomial SVMs

## Data Preprocessing.

In [3]:
cancer = datasets.load_breast_cancer()

In [4]:
df = pd.DataFrame(cancer.data, columns = cancer.feature_names)

In [5]:
df

mean radius  mean texture  mean perimeter  mean area  mean smoothness  \
0          17.99         10.38          122.80     1001.0          0.11840   
1          20.57         17.77          132.90     1326.0          0.08474   
2          19.69         21.25          130.00     1203.0          0.10960   
3          11.42         20.38           77.58      386.1          0.14250   
4          20.29         14.34          135.10     1297.0          0.10030   
..           ...           ...             ...        ...              ...   
564        21.56         22.39          142.00     1479.0          0.11100   
565        20.13         28.25          131.20     1261.0          0.09780   
566        16.60         28.08          108.30      858.1          0.08455   
567        20.60         29.33          140.10     1265.0          0.11780   
568         7.76         24.54           47.92      181.0          0.05263   

     mean compactness  mean concavity  mean concave points  mean symmetry  \
0             0.27760         0.30010              0.14710         0.2419   
1             0.07864         0.08690              0.07017         0.1812   
2             0.15990         0.19740              0.12790         0.2069   
3             0.28390         0.24140              0.10520         0.2597   
4             0.13280         0.19800              0.10430         0.1809   
..                ...             ...                  ...            ...   
564           0.11590         0.24390              0.13890         0.1726   
565           0.10340         0.14400              0.09791         0.1752   
566           0.10230         0.09251              0.05302         0.1590   
567           0.27700         0.35140              0.15200         0.2397   
568           0.04362         0.00000              0.00000         0.1587   

     mean fractal dimension  ...  worst radius  worst texture  \
0                   0.07871  ...        25.380          17.33   
1                   0.05667  ...        24.990          23.41   
2                   0.05999  ...        23.570          25.53   
3                   0.09744  ...        14.910          26.50   
4                   0.05883  ...        22.540          16.67   
..                      ...  ...           ...            ...   
564                 0.05623  ...        25.450          26.40   
565                 0.05533  ...        23.690          38.25   
566                 0.05648  ...        18.980          34.12   
567                 0.07016  ...        25.740          39.42   
568                 0.05884  ...         9.456          30.37   

     worst perimeter  worst area  worst smoothness  worst compactness  \
0             184.60      2019.0           0.16220            0.66560   
1             158.80      1956.0           0.12380            0.18660   
2             152.50      1709.0           0.14440            0.42450   
3              98.87       567.7           0.20980            0.86630   
4             152.20      1575.0           0.13740            0.20500   
..               ...         ...               ...                ...   
564           166.10      2027.0           0.14100            0.21130   
565           155.00      1731.0           0.11660            0.19220   
566           126.70      1124.0           0.11390            0.30940   
567           184.60      1821.0           0.16500            0.86810   
568            59.16       268.6           0.08996            0.06444   

     worst concavity  worst concave points  worst symmetry  \
0             0.7119                0.2654          0.4601   
1             0.2416                0.1860          0.2750   
2             0.4504                0.2430          0.3613   
3             0.6869                0.2575          0.6638   
4             0.4000                0.1625          0.2364   
..               ...                   ...             ...   
564           0.4107                0.2216         

In [6]:
normalized_df=(cancer.data-cancer.data.min())/(cancer.data.max()-cancer.data.min())
#normalized_df=(cancer.data-cancer.data.mean())/cancer.data.std()

In [7]:
normalized_df.min(),normalized_df.max()

(0.0, 1.0)

In [8]:
def check_targets(original_set):
    original_unique = np.unique(original_set)
    print("Original Targets: ",original_unique,"\nDesired Targets: [-1,1]")
    print("Is original the desired [1,-1]? ", np.array_equiv(original_unique,np.array([-1,1])))
    if not np.array_equiv(original_unique,np.array([-1,1])):
        if 1 in original_unique:
            print("1 exists in dataset")
            new = np.select([original_set == original_unique[0]],[-1],original_set)
        elif -1 in original_unique:
            print("-1 exists in dataset")
            new = np.select([original_set == original_unique[1]],[1],original_set)
        else:
            print("Neither exists in dataset")
            new = np.select([original_set == original_unique[0],original_set == original_unique[1]],[-1,1],original_set)
        #indexes = original_set[np.where(original_set == unique_elems[0])]
        print("New datasets consists of: ",np.unique(new))
        return new

In [9]:
targets = check_targets(cancer.target)

Original Targets:  [0 1] 
Desired Targets: [-1,1]
Is original the desired [1,-1]?  False
1 exists in dataset
New datasets consists of:  [-1  1]


## Data Separation and Training

In [10]:
X_train, X_test, y_train, y_test = train_test_split(normalized_df, targets, test_size=0.3,random_state=107) # 70% training and 30% test

In [11]:
def create_linear_classifier(kernel_type='linear'):
    return svm.SVC(kernel=kernel_type)
def create_poly_classifier(kernel_type='poly',my_degree=2,my_gamma=1/30):
    return svm.SVC(kernel=kernel_type, degree = my_degree,gamma=my_gamma)

In [12]:
clf = create_linear_classifier()
poly = create_poly_classifier('poly',2,1/(X_train.var() * len(X_train[0])))

#Train the models using the training sets
clf.fit(X_train, y_train)
poly.fit(X_train, y_train)

#Predict the response for test dataset
y_pred = clf.predict(X_test)
poly_y_pred = poly.predict(X_test)
print("Accuracy Linear:", metrics.accuracy_score(y_test, y_pred))
print("Accuracy Linear:", metrics.accuracy_score(y_test, poly_y_pred))

Accuracy Linear: 0.9064327485380117
Accuracy Linear: 0.9532163742690059


In [13]:
y_pred_train = clf.predict(X_train)
poly_pred_train = poly.predict(X_train)
print("Accuracy on Training:", metrics.accuracy_score(y_train, y_pred_train))
print("Accuracy on Training:", metrics.accuracy_score(y_train, poly_pred_train))

Accuracy on Training: 0.8592964824120602
Accuracy on Training: 0.8944723618090452


## SVM Decision Function For The First Element of Training Dataset

In [14]:
#Sum (coef @ sup_vec @ X[index] + bias)
((clf.dual_coef_ @ clf.support_vectors_) @ X_train[0].reshape(1, len(X_train[0])).T + clf.intercept_)[0][0]

0.48607829979011963

In [15]:
(poly.dual_coef_ @ (((poly.support_vectors_ @ X_train[0].reshape(1, len(X_train[0])).T) * poly.gamma + poly.coef0) ** poly.degree) + poly.intercept_)[0][0]

0.38923397985272157

In [16]:
#Linear SVM Decision Function
print("DualCoef / Support Vectors / X_Train.T Reshaped / Intercept (bias)")
clf.dual_coef_.shape, clf.support_vectors_.shape, X_train[0].reshape(1, len(X_train[0])).T.shape, clf.intercept_.shape

DualCoef / Support Vectors / X_Train.T Reshaped / Intercept (bias)


((1, 194), (194, 30), (30, 1), (1,))

In [17]:
#Polynomial SVM Decision Function
print("DualCoef / Support Vectors / X_Train.T Reshaped / Gamma / Coef0 / Degree / Intercept (bias)")
poly.dual_coef_.shape, poly.support_vectors_.shape, X_train[0].reshape(1, len(X_train[0])).T.shape,poly.gamma, poly.coef0, poly.degree, poly.intercept_

DualCoef / Support Vectors / X_Train.T Reshaped / Gamma / Coef0 / Degree / Intercept (bias)


((1, 113), (113, 30), (30, 1), 11.771764103829, 0.0, 2, array([2.36559509]))

# Defining Thresholds and Finding Rejecteds

In [18]:
def limits(classifier,data):
    dec_fun = classifier.decision_function(data)
    lim_pos = dec_fun[np.argmax(dec_fun)]
    lim_neg = dec_fun[np.argmin(dec_fun)]
    return dec_fun, lim_pos, lim_neg

In [19]:
def find_thresholds(decfun,t1,t2,wr,chosen_min='EWRR'):
    solution = {'WR':0,'T1':0, 'T2':0,'E':0,'R':0,'EWRR':0}
    index = None
    n_elements = decfun.shape[0]
    for i,wr_ in enumerate(wr):
      for j in range(0,len(t1)):
        #Get Number of Rejected
        positive_indexes = np.where(decfun >= t1[j])
        negative_indexes = np.where(decfun < t2[j])
        rejected_indexes = np.where((decfun < t1[j]) & (decfun >= t2[j]))
        R = rejected_indexes[0].shape[0]
        #np.array(positive_indexes).shape,np.array(negative_indexes).shape, R

        #Get Number of Misclassifications
        class_p = y_train[positive_indexes]
        class_n = y_train[negative_indexes]
        error_p = np.where(class_p == np.unique(y_train)[0])[0].shape[0]
        error_n = np.where(class_n == np.unique(y_train)[1])[0].shape[0]
        E = (error_p + error_n)/(n_elements - R)
        if chosen_min=='R':
            if (i == 0 and i == j) or R < solution['R']:
                solution['WR'] = wr_
                solution['T1'] = t1[j]
                solution['T2'] = t2[j]
                solution['E'] = E
                solution['R'] = R
                solution['EWRR'] = E + wr_ * R
        elif chosen_min=='E':
            if (i == 0 and i == j) or E < solution['E']:
                solution['WR'] = wr_
                solution['T1'] = t1[j]
                solution['T2'] = t2[j]
                solution['E'] = E
                solution['R'] = R
                solution['EWRR'] = E + wr_ * R
        elif chosen_min=='EWRR':
            if (i == 0 and i == j) or (E + wr_ * R) < solution['EWRR']:
                solution['WR'] = wr_
                solution['T1'] = t1[j]
                solution['T2'] = t2[j]
                solution['E'] = E
                solution['R'] = R
                solution['EWRR'] = E + wr_ * R
        else:
            return 'Chosen option "' +chosen_min+'" is invalid'
    print('Thresholds by min(',chosen_min,') from solution: ',solution)
    return solution['T1'], solution['T2']      
                

In [20]:
def find_indexes(decfun,t1,t2):
    positive_indexes = np.where(decfun >= t1)[0]
    negative_indexes = np.where(decfun < t2)[0]
    rejected_indexes = np.where((decfun < t1) & (decfun >= t2))[0]
    R = rejected_indexes.shape[0]
    return positive_indexes,negative_indexes,rejected_indexes

In [21]:
def find_thresholds_and_indexes(classifier,data,wr = None):  
    dec_fun,lim_pos,lim_neg = limits(classifier,data)
    if wr == None:
        wr = [0.04, 0.08, 0.12, 0.16, 0.2, 0.24, 0.28, 0.32, 0.36, 0.4, 0.44, 0.48]
    t1 = []
    t2 = []
    for i in range (1,21):
      t1.append(0.05*i*lim_pos)
      t2.append(0.05*i*lim_neg)  
    T1,T2 = find_thresholds(dec_fun,t1,t2,wr)
    pos_idx,neg_idx,rej_idx = find_indexes(dec_fun,T1,T2)
    return T1, T2, pos_idx, neg_idx, rej_idx

# Implementing SVM function for Z3 Solver

## Z3 Decision Function Elements

In [22]:
np.RealVal = np.vectorize(RealVal) 
np.RealVector = np.vectorize(RealVector) 

In [23]:
def to_z3_conversion(classifier,training_set):
    z3_dual_coef = np.RealVal(classifier.dual_coef_)
    z3_support_vectors = np.RealVal(classifier.support_vectors_)
    z3_intercept_ = np.RealVal(classifier.intercept_)
    z3_X_Train = np.RealVector('x',training_set.shape[1])
    if classifier.kernel == 'poly':
        z3_gamma = np.RealVal(classifier.gamma)
        z3_coef0 = np.RealVal(classifier.coef0)
        z3_degree = np.RealVal(classifier.degree)
        return z3_dual_coef,z3_support_vectors,z3_intercept_,z3_X_Train, z3_gamma,z3_coef0,z3_degree
    return z3_dual_coef,z3_support_vectors,z3_intercept_,z3_X_Train

# Z3 with Reject Option

## Explaining the Classifier's Decision Function and Finding Relevant Features

In [24]:
def z3_explanation(classifier,t1, t2, X, z3_coef, z3_sup_vec, z3_X, z3_intercept, reject_indexes, z3_gamma = None, z3_coef0 = None, z3_degree = None, show_values=False):
    relevant = []
    irrelevant = []
    global_values = []
    print("Number of Rejected: ", len(reject_indexes))
    solver = Solver()
    if classifier.kernel=='linear':
        solver.add(Or(((z3_coef @ z3_sup_vec) @ z3_X.reshape(1, len(z3_X)).T + z3_intercept)[0][0] >= t1,
                      ((z3_coef @ z3_sup_vec) @ z3_X.reshape(1, len(z3_X)).T + z3_intercept)[0][0] < t2))
    elif classifier.kernel=='poly':
        solver.add(Or(((z3_dual_coef @ (((z3_support_vectors @ z3_X.reshape(1, len(z3_X)).T) * z3_gamma + z3_coef0) ** z3_degree) + z3_intercept_)[0][0] >= t1),
                      (z3_dual_coef @ (((z3_support_vectors @ z3_X.reshape(1, len(z3_X)).T) * z3_gamma + z3_coef0) ** z3_degree) + z3_intercept_)[0][0] < t2))
    for j in range(0, len(z3_X)):
        solver.add(z3_X[j] >= 0)
        solver.add(z3_X[j] <= 1)
    solver.push()
    for i in range(0, len(reject_indexes)):
        # Add Assertions for 0<= feature <= 1
        index_list = list(range(len(z3_X)))
        unsat_list = []
        sat_list = []
        values = []

        # Select a feature and unfix it
        for z in range(0, len(z3_X)):
            for j in range(0, len(z3_X)):
                if j != z and j in index_list:  # Choose one to check influence
                    solver.add(z3_X[j] == X[reject_indexes[i]][j])

            check = solver.check()
            if check == sat:
                model = solver.model()
                value = model[z3_X[z]].numerator_as_long() / model[z3_X[z]].denominator_as_long()
                sat_list.append(z)
                values.append(value)
                if show_values:
                    print('i = ', i, z, check, X[reject_indexes[i]][z], value)
            else:
                unsat_list.append(z)
                index_list.remove(z)
                if show_values:
                    print('i = ', i, z, check)
            solver.pop()
            solver.push()
        print("Finished ", i)
        relevant.append(sat_list)
        irrelevant.append(unsat_list)
        global_values.append(values)
        # print("Relevant: ",sat_list, '\nUnsat List: ',unsat_list,'\n')     
    for i in range(0, len(relevant)):
        print('Rejected ', i, '\nRelevant Features: ', relevant[i], '\nValues: ', global_values[i], '\nIrrelevant Features: ',
              irrelevant[i], '\n\n')
        if classifier.kernel=='poly':
            print('é poly')
            
    return relevant, irrelevant

### For Linear Classifier

#### Get thresholds and the rejected for Linear

In [25]:
T1,T2, positive_indexes,negative_indexes,rejected_indexes = find_thresholds_and_indexes(clf,X_train)
#T1,T2, positive_indexes.shape[0],negative_indexes.shape[0],rejected_indexes.shape[0]

Thresholds by min( EWRR ) from solution:  {'WR': 0.04, 'T1': 0.09337685074882902, 'T2': -0.33001855620878895, 'E': 0.1345646437994723, 'R': 19, 'EWRR': 0.8945646437994723}


#### Get Z3's equivalent to linear classifier's decision function

In [26]:
z3_dual_coef,z3_support_vectors,z3_intercept_,z3_X_Train = to_z3_conversion(clf,X_train)

In [27]:
linear_relevant, linear_irrelevant = z3_explanation(clf,T1,T2,X_train,z3_dual_coef,z3_support_vectors,z3_X_Train,z3_intercept_,rejected_indexes, show_values=False)

Number of Rejected:  19
Finished  0
Finished  1
Finished  2
Finished  3
Finished  4
Finished  5
Finished  6
Finished  7
Finished  8
Finished  9
Finished  10
Finished  11
Finished  12
Finished  13
Finished  14
Finished  15
Finished  16
Finished  17
Finished  18
Rejected  0 
Relevant Features:  [3, 8, 10, 11, 12, 13, 16, 17, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29] 
Values:  [0.5696957675146821, 1.0, 1.0, 0.5413918567012442, 0.5070781646325205, 0.5052261025127721, 1.0, 0.8111025521271286, 1.0, 0.5022261443098118, 0.5032246152027775, 0.5149409757592878, 0.4022635227887488, 0.5014852145439304, 0.5003039367567866, 0.5002330805229445, 0.5005994016970484, 0.5007296236731065, 0.5023131925464672] 
Irrelevant Features:  [0, 1, 2, 4, 5, 6, 7, 9, 14, 15, 18] 


Rejected  1 
Relevant Features:  [0, 1, 2, 3, 12, 13, 20, 21, 22, 23, 25, 26, 27, 28] 
Values:  [1.0, 0.6167166357708477, 0.542956214013805, 0.48335253977189596, 0.7955986242364118, 0.5127960571080458, 0.6296467245774282, 0.5675071558807

### For Polynomial Classifier (WIP)

#### Get thresholds and the rejected for Poly

In [28]:
#T1,T2, positive_indexes,negative_indexes,rejected_indexes = find_thresholds_and_indexes(poly,X_train)
#T1,T2, positive_indexes.shape[0],negative_indexes.shape[0],rejected_indexes.shape[0]

#### Get Z3's equivalent to Poly classifier's decision function

In [29]:
#z3_dual_coef,z3_support_vectors,z3_intercept_,z3_X_Train,z3_gamma,z3_coef0,z3_degree = to_z3_conversion(poly,X_train)

In [30]:
#poly_relevant, poly_irrelevant = z3_explanation(poly,T1,T2,X_train,z3_dual_coef,z3_support_vectors,z3_X_Train,z3_intercept_,rejected_indexes[0:1], z3_gamma,z3_coef0,z3_degree, show_values=False)

# Anchors

## Setting Up

In [31]:
from __future__ import print_function
import sys
import sklearn
import sklearn.ensemble
from anchor import utils
from anchor import anchor_tabular

In [32]:
def generate_ro_target_set(target_set,rejected_indexes):
    target_set[rejected_indexes] = 0
    return target_set

In [33]:
ro_set = generate_ro_target_set(y_train,rejected_indexes)
print(np.unique(ro_set))

[-1  0  1]


In [52]:
feature_list = []
for i in range(0,len(X_train[0])):
    feature_list.append(str(i))
feature_list = np.array(feature_list)

In [53]:
explainer = anchor_tabular.AnchorTabularExplainer(
    [-1,0,1],
    feature_list,
    X_train)

In [54]:
def svm_decfun(data,classifier=clf):
    data = np.atleast_2d(data)
    return ((classifier.dual_coef_ @ classifier.support_vectors_) @ data.T + classifier.intercept_)[0][0]
print(svm_decfun(X_train[rejected_indexes[0]]))

0.03553746598762597


In [55]:
def svm_decfun_class(data,classifier=clf,Threshold_1=T1,Threshold_2=T2):
    if svm_decfun(data) >= Threshold_1:
        return np.array([2]) #class 1, since [-1, 0, 1]
    elif svm_decfun(data) < Threshold_2:
        return np.array([0]) #class -1
    else:
        return np.array([1]) #class 0
    
print(svm_decfun_class(X_train[rejected_indexes[0]]))

[1]


## Explanation for 1 Instance

### Anchors Explanation

In [56]:
idx = rejected_indexes[0]
np.random.seed(1)
print('Prediction: ', explainer.class_names[svm_decfun_class(X_train[idx])[0]])
exp = explainer.explain_instance(X_train[idx], svm_decfun_class, threshold=1)

Prediction:  0


In [57]:
print('Anchor: %s' % (' AND '.join(exp.names())))
print('Precision: %.2f' % exp.precision())
print('Coverage: %.2f' % exp.coverage())

Anchor: 9 > 0.00 AND 0.00 < 11 <= 0.00 AND 0.00 < 0 <= 0.00 AND 20 > 0.00 AND 0.02 < 2 <= 0.02 AND 0.00 < 19 <= 0.00 AND 0.00 < 14 <= 0.00 AND 0.00 < 15 <= 0.00 AND 0.00 < 16 <= 0.00 AND 0.00 < 17 <= 0.00 AND 0.13 < 3 <= 0.18 AND 0.00 < 18 <= 0.00 AND 23 > 0.24 AND 6 > 0.00 AND 27 > 0.00 AND 22 > 0.03 AND 7 > 0.00 AND 0.01 < 13 <= 0.01 AND 26 > 0.00 AND 5 > 0.00 AND 25 > 0.00 AND 0.00 < 12 <= 0.00 AND 4 > 0.00 AND 0.01 < 21 <= 0.01 AND 0.00 < 1 <= 0.00 AND 28 > 0.00 AND 0.00 < 10 <= 0.00 AND 24 > 0.00 AND 8 > 0.00 AND 29 > 0.00
Precision: 0.49
Coverage: 0.00


In [58]:
exp.show_in_notebook()

In [70]:
restrictions = exp.names()

### Anchors Explanation on Z3 - WIP

In [79]:
import re

In [ ]:
print('Started')
for idx in negative_indexes:
  exp = explainer.explain_instance(X_train[idx], svm_decfun_class, threshold=1)
  restrictions = [name.split(' ') for name in exp.names()]
  print('\n--------------\nIndex = ',idx)
  for restriction in restrictions:
    if '<' in restriction and '<=' not in restriction:
        #print(len(restriction),'Only <',restriction)
        pass
    elif '<' in restriction and '<=' in restriction:
        #print(len(restriction),'< and <=',restriction)
        pass
    elif '<=' in restriction and len(restriction)==3:
        #print(len(restriction),'Only <=',restriction)
        pass
    
    elif '>' in restriction and '>=' not in restriction:
        #print(len(restriction),'Only >',restriction)
        pass
    elif '>' in restriction and '>=' in restriction:
        #print(len(restriction),'> AND >=',restriction)
        pass
    elif  '>=' in restriction and len(restriction)==3:
        #print(len(restriction),'Only >=',restriction)
        pass
    
    else:
        print("RESTRIÇÃO NÃO TRATADA",restriction)

Started

--------------
Index =  3

--------------
Index =  5

--------------
Index =  11

--------------
Index =  12

--------------
Index =  15

--------------
Index =  19

--------------
Index =  22

--------------
Index =  25

--------------
Index =  32

--------------
Index =  33

--------------
Index =  37

--------------
Index =  38

--------------
Index =  42

--------------
Index =  52

--------------
Index =  55

--------------
Index =  57

--------------
Index =  68

--------------
Index =  69

--------------
Index =  77

--------------
Index =  84

--------------
Index =  103

--------------
Index =  106

--------------
Index =  110

--------------
Index =  114

--------------
Index =  118

--------------
Index =  119

--------------
Index =  132

--------------
Index =  140

--------------
Index =  145

--------------
Index =  151

--------------
Index =  156

--------------
Index =  158

--------------
Index =  162

--------------
Index =  166

--------------
Index =  168

## Explanation for Multiple Instances - WIP